# 1. Map download

Download the cycling network from OpenStreetMap using osmnx

In [1]:
_base_excludes = (
    '["area"!="yes"]'
    '["access"!="no"]'
    # no destroyed roads
    '[!"razed"][!"razed:highway"][!"demolished:highway"][!"removed:highway"]'
    # rail/water/indoor are inacccessible by bike
    '[!"railway"]'
    '[!"waterway"]'
    '["route"!="ferry"]'
    '["indoor"!="yes"]'
    # practically untraversable routes
    '["mtb:scale"!="6"]'
)
_excludes_ignoring_bicycle_tag = (
    # Exclude limited access roads
    '["access"!~"^(private|customers|military|delivery|emergency|no)$"]'
    # no big highways
    '["motorroad"!="yes"]'
    # exclude golf courses
    '["golf_cart"!~"^(yes|designated|private)$"]'
    # practically untraversable routes
    '["mtb:scale"!="6"]'
    # no tunnels - although this has some false positives for short tunnels that are
    # in fact part of bikeable roads
    # TODO: postprocess filter tunnels by length instead?
    # '["tunnel"!~"^(yes|building_passage)$"]'
)
_bicycle_tag_excludes = '["bicycle"!~"^(dismount|use_sidepath|private|no)$"]'
excludes = _base_excludes + _excludes_ignoring_bicycle_tag + _bicycle_tag_excludes


# 1. Start with road types that can be *assumed* to have bicycle access,
#    unless otherwise specified.
assumed_bike_access = [
    (
        '["highway"]'
        '["highway"!~"^(motorway|motorway_link|steps|stairs|escalator|elevator|construction|proposed|demolished|escape|bus_guideway|platform|elevator|raceway|rest_area|traffic_island|services|yes|no|razed|corridor|busway|via_ferrata)$"]'
        '["highway"!~"^(trunk|trunk_link|footway|service|bridleway)$"]'
        '["highway"!="pedestrian"]'
        f"{excludes}"
    ),
    ## **Named** service roads that don’t have a specific service=... tag
    f'["highway"="service"]["name"][!"service"]{excludes}',
]

# 2. Add in ways that have bicycle access explicitly marked
explicit_bike_access = [
    # Ways with allowed values in bicycle=... tags
    f'["highway"]["bicycle"~"^(yes|designated|permissive|official|mtb|MTB)$"]{_base_excludes}',
    # Ways with bicycle:designated... tags
    f'["highway"][~"^bicycle:designated.*$"~"."]{excludes}',
    # Ways with a `highway` tag of cycleway
    f'["highway"="cycleway"]{excludes}',
    # Ways marked with bicycle_road/cyclestreet
    f'["highway"][~"^(bicycle_road|cyclestreet)$"~"."]{excludes}',
    # Ways with `bicycle:no` but `bicycle:conditional`
    f'["highway"]["bicycle:conditional"~"^yes"]{_excludes_ignoring_bicycle_tag}',
    # Ways that are part of relations with route=bicycle
    # We do some Overpass query injection to query for relations
    # f'(1)(2);relation["route"="bicycle"]'
]

bike_filter = assumed_bike_access + explicit_bike_access

In [2]:
import osmnx as ox
import osmnx.settings

osmnx.settings.useful_tags_way = ["name", "highway", "access", "oneway", "ref", "bicycle"]

bike_network_directed = ox.simplify_graph(
    ox.graph_from_place(
        "Manhattan, New York, USA",
        custom_filter=bike_filter,
        simplify=False,
        retain_all=True,
        truncate_by_edge=True,
    ),
    edge_attrs_differ=["osmid"],
)

In [3]:
edges_gdf = ox.convert.graph_to_gdfs(bike_network_directed, nodes=False)
edges_gdf = edges_gdf[edges_gdf["reversed"] != True] # Drop duplicate edges that go “backwards” down a two-way street
edges_gdf["osmid"] = edges_gdf["osmid"].astype(str)
edges_gdf

osmid               name      highway  \
u           v           key                                               
42421728    4205830390  0     420625573  West 106th Street    secondary   
            11807757983 0    1271523198  Central Park West    secondary   
42421731    42432737    0     195743186   Manhattan Avenue  residential   
            4205830392  0     420625570  West 106th Street    secondary   
42421737    42437917    0     420625563    Columbus Avenue      primary   
...                                 ...                ...          ...   
12875266421 12875266420 0    1390944998                NaN   pedestrian   
            4080363917  0     405898226           Hay Road   pedestrian   
12958552132 8438533307  0     908825267                NaN      footway   
            12958552118 0    1410267537                NaN      footway   
            12958552137 0    1410267538                NaN      footway   

                                bicycle  oneway  reversed      length  \
u           v           key                                             
42421728    4205830390  0           yes   False     False   36.526891   
            11807757983 0           yes   False     False   35.582045   
42421731    42432737    0           NaN   False     False   85.968765   
            4205830392  0           yes   False     False   63.515790   
42421737    42437917    0           NaN    True     False   85.990854   
...                                 ...     ...       ...         ...   
12875266421 12875266420 0    designated   False     False    7.851026   
            4080363917  0    designated   False     False   12.598066   
12958552132 8438533307  0    designated   False     False  117.907836   
            12958552118 0    designated   False     False   37.489153   
            12958552137 0    designated   False     False   34.051054   

                                                                      geometry  \
u           v           key                                                      
42421728    4205830390  0    LINESTRING (-73.96004 40.79805, -73.96017 40.7...   
            11807757983 0    LINESTRING (-73.96004 40.79805, -73.95997 40.7...   
42421731    42432737    0    LINESTRING (-73.96147 40.79865, -73.9614 40.79...   
            4205830392  0    LINESTRING (-73.96147 40.79865, -73.96158 40.7...   
42421737    42437917    0    LINESTRING (-73.96287 40.79924, -73.96294 40.7...   
...                                                                        ...   
12875266421 12875266420 0    LINESTRING (-74.01893 40.69221, -74.01884 40.6...   
            4080363917  0    LINESTRING (-74.01893 40.69221, -74.01893 40.6...   
12958552132 8438533307  0    LINESTRING (-73.97653 40.71408, -73.97665 40.7...   
            12958552118 0    LINESTRING (-73.97653 40.71408, -73.97648 40.7...   
            12958552137 0    LINESTRING (-73.97653 40.71408, -73.97646 40.7...   

                             ref access  
u           v           key              
42421728    4205830390  0    NaN    NaN  
            11807757983 0    NaN    NaN  
42421731    42432737    0    NaN    NaN  
            4205830392  0    NaN    NaN  
42421737    42437917    0    NaN    NaN  
...                          ...    ...  
12875266421 12875266420 0    NaN    NaN  
            4080363917  0    NaN    NaN  
12958552132 8438533307  0    NaN    NaN  
            12958552118 0    NaN    NaN  
            12958552137 0    NaN    NaN  

[11525 rows x 10 columns]

In [4]:
import folium

edges_map = folium.Map(tiles="CartoDB dark_matter")
folium.GeoJson(
    edges_gdf,
    lambda _: {"color": "#ffffff", "weight": 2, "fill": False, "opacity": 0.5},
    popup=folium.GeoJsonPopup(fields=["osmid", "name", "highway", ]),
).add_to(edges_map)

edges_map.fit_bounds(edges_map.get_bounds())
edges_map

# 2. GPS track

In [5]:
import fitparse
import geopandas as gpd

def load_track(path: str):
    fitfile = fitparse.FitFile(path)
    # TODO: split into multiple dataframes where there was a pause of more than a few seconds
    entries = gpd.GeoDataFrame(
        record.get_values()
        for record in fitfile.get_messages("record")
        if isinstance(record, fitparse.DataMessage)
    )
    entries["lat"] = entries["position_lat"] * (180 / 2**31)
    entries["lng"] = entries["position_long"] * (180 / 2**31)

    # TODO: convert timestamp from string to datetime
    # TODO: sort by timestamp

    track = (
        entries.drop(columns=["position_lat", "position_long"])
        .set_geometry(gpd.points_from_xy(entries["lng"], entries["lat"]), crs="wgs84")
        .dropna(subset=["lat", "lng"])
        .drop(columns=["lat", "lng", "altitude"])
        .rename(columns={"enhanced_altitude": "altitude", "enhanced_speed": "speed"})
    )

    return track

track = load_track("testdata/track2.fit")
track

timestamp  gps_accuracy  altitude  distance  speed  heart_rate  \
0    2025-06-12 14:19:09           4.0      19.2      0.00  1.693         NaN   
1    2025-06-12 14:19:10           4.0      19.2      1.69  2.116         NaN   
2    2025-06-12 14:19:11           4.0      19.2      4.23  2.856         NaN   
3    2025-06-12 14:19:12           4.0      19.0      7.41  3.504         NaN   
4    2025-06-12 14:19:13           3.0      19.0     11.24  3.757         NaN   
...                  ...           ...       ...       ...    ...         ...   
2985 2025-06-12 15:11:16           4.0       8.4  19812.43  1.798         NaN   
2986 2025-06-12 15:11:17           4.0       8.4  19813.55  0.868         NaN   
2987 2025-06-12 15:11:18           4.0       8.4  19814.16  1.142         NaN   
2988 2025-06-12 15:11:19           4.0       8.4  19814.16    NaN         NaN   
2989 2025-06-12 15:11:20           5.0       8.4  19814.16    NaN         NaN   

                        geometry  
0      POINT (-73.97408 40.7946)  
1     POINT (-73.97412 40.79462)  
2     POINT (-73.97416 40.79464)  
3     POINT (-73.97421 40.79465)  
4     POINT (-73.97425 40.79467)  
...                          ...  
2985  POINT (-74.00693 40.74151)  
2986  POINT (-74.00696 40.74151)  
2987  POINT (-74.00699 40.74151)  
2988  POINT (-74.00701 40.74151)  
2989   POINT (-74.00703 40.7415)  

[2989 rows x 7 columns]

In [6]:
import folium
import shapely

track_map = folium.Map(tiles="CartoDB.DarkMatter")
folium.GeoJson(
    track[["geometry", "distance", "speed", "heart_rate"]],
    marker=folium.CircleMarker(radius=4),
).add_to(track_map)

track_linestring = shapely.geometry.LineString(track["geometry"])
folium.GeoJson(track_linestring, lambda _: { "color": "#ff0" }).add_to(track_map)
track_map.fit_bounds(track_map.get_bounds())
track_map

# 3. Matching GPS track to street network
## 3.1 Projection
Start by projecting data into an appropriate UTM CRS in order to work with coordinates that are measured with real-world units (meters) rather than lat/lng degrees

In [7]:
from pyproj import Transformer

crs = track.estimate_utm_crs()

transformer_to_meters = Transformer.from_crs("wgs84", crs, always_xy=True)
transformer_to_latlng = Transformer.from_crs(crs, "wgs84", always_xy=True)

crs

<Projected CRS: EPSG:32618>
Name: WGS 84 / UTM zone 18N
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: Between 78°W and 72°W, northern hemisphere between equator and 84°N, onshore and offshore. Bahamas. Canada - Nunavut; Ontario; Quebec. Colombia. Cuba. Ecuador. Greenland. Haiti. Jamaica. Panama. Turks and Caicos Islands. United States (USA). Venezuela.
- bounds: (-78.0, 0.0, -72.0, 84.0)
Coordinate Operation:
- name: UTM zone 18N
- method: Transverse Mercator
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [8]:
edges_gdf_proj = edges_gdf.to_crs(crs)
track_proj = track.to_crs(crs)

## 3.2 Snapping points to street network

In [9]:
import pandas as pd

def get_edges_for_point(
    point_proj: shapely.Point,
    radius: int,
):
    # Find all edges that intersect within radius of point
    matched_edges = edges_gdf_proj.iloc[edges_gdf_proj["geometry"].sindex.query(
        point_proj,
        predicate="dwithin",
        distance=radius,
    )]
    # compute distance to each
    def get_match_geom(edge_geom):
        shortest_line = shapely.shortest_line(a=point_proj, b=edge_geom)
        matched_point = shapely.Point(shortest_line.coords[1])
        return pd.Series({
            "matched_point": matched_point,
            "distance_from_search": shapely.length(shortest_line),
            "distance_along_edge": shapely.line_locate_point(edge_geom, matched_point, normalized=True)
        })


    if len(matched_edges):
        return matched_edges.join(matched_edges["geometry"].apply(get_match_geom))
    return matched_edges


# Example
point_1 = track_proj.iloc[0]["geometry"]
matched_edges_1 = get_edges_for_point(point_1, 30)
matched_edges_1

osmid              name    highway bicycle  \
u          v        key                                                   
7818397401 42431096 0    837696075   West End Avenue   tertiary     NaN   
7132609426 42431096 0    763303893  West 95th Street  secondary     NaN   

                         oneway  reversed     length  \
u          v        key                                
7818397401 42431096 0     False     False  47.255754   
7132609426 42431096 0      True     False  84.180662   

                                                                  geometry  \
u          v        key                                                      
7818397401 42431096 0    LINESTRING (586558.814 4516419.906, 586577.5 4...   
7132609426 42431096 0    LINESTRING (586506.202 4516500.304, 586530.42 ...   

                         ref access  \
u          v        key               
7818397401 42431096 0    NaN    NaN   
7132609426 42431096 0    NaN    NaN   

                                                       matched_point  \
u          v        key                                                
7818397401 42431096 0     POINT (586574.3319056142 4516448.86293034)   
7132609426 42431096 0    POINT (586555.7073569815 4516474.714169165)   

                         distance_from_search  distance_along_edge  
u          v        key                                             
7818397401 42431096 0               28.419014             0.695728  
7132609426 42431096 0               13.989920             0.661091

In [10]:
# example visualization
matched_edges_map = folium.Map(tiles="CartoDB.DarkMatter")
# plot original point
folium.Marker(
    location=transformer_to_latlng.transform(point_1.x, point_1.y)[::-1]
).add_to(matched_edges_map)
# plot “matched points” on matched edges
matched_point_df = matched_edges_1.set_geometry("matched_point", crs=matched_edges_1.crs)[["matched_point"]]
folium.GeoJson(
    matched_point_df,
    marker=folium.CircleMarker(radius=5, color="red"),
).add_to(matched_edges_map)
# plot dotted lines between original point and matched points
folium.GeoJson(
    matched_point_df["matched_point"].apply(
        lambda point_2: shapely.LineString([point_1, point_2])
    ).to_frame(),
    style={ "color": "red", "dashArray": "5" }
).add_to(matched_edges_map)
# plot matched edges
folium.GeoJson(matched_edges_1[["geometry"]]).add_to(matched_edges_map)

matched_edges_map.fit_bounds(matched_edges_map.get_bounds())
matched_edges_map

In [11]:
# At every point on the graph there are one or more possible “matches”
#   - the closest point along zero or more matched edges
#   - the track point itself, ie no match at all—“leaving” the street network.

EDGE_SEARCH_DISTANCE = 50  # meters

nodes_for_track_points = {
    # track_point_index -> [
    #   { "point": POINT(x, y), "edge": (u,v,key), "distance_from_track": d },
    #   { "point": POINT(x, y), "edge": None, "distance_from_track": 0 },
    # ]
}


for _idx, _track_entry in track_proj.iterrows():
    nodes_here = []

    # the track point itself, “free” (unconstrained) from the street network—
    # this means “leaving” the street network
    # this is needed, for example, to accurately match routes that “cut across”
    nodes_here.append({
        "point": _track_entry["geometry"],
        "edge": None,
        "distance_from_track": 0,
    })

    # candidate points on the street network
    for (_uvk, _match) in get_edges_for_point(_track_entry["geometry"], EDGE_SEARCH_DISTANCE).iterrows():
        nodes_here.append({
            "point": _match["matched_point"],
            "edge": _uvk,
            "osmid": _match["osmid"],
            "edge_position": _match["distance_along_edge"],
            "distance_from_track": _match["distance_from_search"],
        })

    nodes_here.sort(key=lambda x: x["distance_from_track"])
    nodes_for_track_points[_idx] = nodes_here

# sample: first 5 entries
for _i, (_k, _v) in enumerate(nodes_for_track_points.items()):
    if _i >= 5: break
    print(f"{_k}:")
    for _node in _v[:3]:
        print("  -", _node)

0:
  - {'point': <POINT (586549.283 4516462.287)>, 'edge': None, 'distance_from_track': 0}
  - {'point': <POINT (586555.707 4516474.714)>, 'edge': (7132609426, 42431096, 0), 'osmid': '763303893', 'edge_position': 0.6610914690695046, 'distance_from_track': 13.98991969246725}
  - {'point': <POINT (586574.332 4516448.863)>, 'edge': (7818397401, 42431096, 0), 'osmid': '837696075', 'edge_position': 0.6957279693746626, 'distance_from_track': 28.419014094911898}
1:
  - {'point': <POINT (586545.823 4516464.284)>, 'edge': None, 'distance_from_track': 0}
  - {'point': <POINT (586552.162 4516476.547)>, 'edge': (7132609426, 42431096, 0), 'osmid': '763303893', 'edge_position': 0.6137433315356692, 'distance_from_track': 13.804591089405752}
  - {'point': <POINT (586574.391 4516448.974)>, 'edge': (7818397401, 42431096, 0), 'osmid': '837696075', 'edge_position': 0.6983976564606611, 'distance_from_track': 32.41265462700385}
2:
  - {'point': <POINT (586542.298 4516466.309)>, 'edge': None, 'distance_from_